# A price analysis of coffee

- cpc = cost per cup (18gr of coffee per cup)
- cpc_250g = cost per cup when buying 250g bag (13.88 cups per bag)
- cpc_1kg = cost per cup when buying 1kg bag (55.55 cups per bag)

All prices in €, as of march 1, 2024, as found on the brand websites.

11 shops, 86 coffees in total

In [1]:
import pandas as pd
import numpy as np
import plotly.express as px

pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

df = pd.read_csv("coffee.csv")

#convert euros to float
df['250gr'] = df['250gr'].replace('[^\d.]', '', regex=True).astype(float)
df['1kg'] = df['1kg'].replace('[^\d.]', '', regex=True).astype(float)
df['cpc_250g'] = df['cpc_250g'].replace('[^\d.]', '', regex=True).astype(float)
df['cpc_1kg'] = df['cpc_1kg'].replace('[^\d.]', '', regex=True).astype(float)

df


shop                                  name  \
0     coffee circle                           house blend   
1     coffee circle                                sidamo   
2     coffee circle                               cerrado   
3     coffee circle                  tiga terra omniroast   
4     coffee circle                          yirga santos   
5     coffee circle                                 pacas   
6     coffee circle                    feliciano castillo   
7     coffee circle                        espresso chire   
8     coffee circle                            grano gayo   
9     coffee circle                       francisco lopez   
10    coffee circle                        espresso decaf   
11    coffee circle                    yirga santos decaf   
12            fjord                           house blend   
13            fjord                          samii aricha   
14            fjord                                kii ab   
15            fjord                         puente solaya   
16            fjord                       fes red bourbon   
17            fjord                               mi mina   
18            fjord                     francisco becerra   
19    five elephant                           house blend   
20    five elephant                         cyesha washed   
21    five elephant                           nandi hills   
22    five elephant                      decaf omni roast   
23   bonanza coffee                                 blend   
24   bonanza coffee                               nairobi   
25   bonanza coffee                            kathima ab   
26   bonanza coffee                       finca rabanales   
27   bonanza coffee                             caballero   
28   bonanza coffee                        samii chelbesa   
29   bonanza coffee                                gogogu   
30   bonanza coffee                   sitio vargem grande   
31   bonanza coffee                             el carmen   
32   bonanza coffee                            dark roast   
33         the barn                             boa vista   
34         the barn                            cruz gorda   
35         the barn                             la colina   
36         the barn                                gigesa   
37         the barn                             caballero   
38         the barn                           giakanja ab   
39         the barn                         huye mountain   
40         the barn                   mohamed ali natural   
41         the barn               daterra reserve low caf   
42         19 grams  Café des Mamas - Women's Day Special   
43         19 grams                  los tres potros SL28   
44         19 grams                            la montana   
45         19 grams                          la esperanza   
46         19 grams                            orang utan   
47         19 grams                                 decaf   
48         19 grams                         wild at heart   
49         19 grams                        endless summer   
50         19 grams                         little flower   
51         19 grams                           italo disco   
52          populus                         guji highland   
53          populus                             luz maria   
54          populus                          khalid shifa   
55          populus                       oreti estate aa   
56          populus                          andrade bros   
57          populus                              big shot   
58          populus                             zeitgeist   
59          populus                    peace easy (decaf)   
60             cebe                        santa catarina   
61             cebe                                sonara   
62             cebe                                danisa   
63             cebe                            cuzcatleco   
64             cebe                               

# Country count


In [2]:
split_countries = df['country'].str.split(',')
all_countries = [country.strip().title() for sublist in split_countries.dropna() for country in sublist]
country_counts = pd.Series(all_countries).value_counts()
country_counts = country_counts.reset_index()
#country_counts

In [3]:
df_singleorigin = df[df['type'] == 'so']
fig = px.box(df_singleorigin, x='country', y='cpc_1kg', title='Distribution of Coffee Prices by Country (single origin only)')
fig.update_layout(xaxis_title='country', yaxis_title='cpc_1kg', xaxis_tickangle=-45)
fig.show()

# Brand: average price per brand
cost per cup when buying 1kg bags

just checking which brands are more expensive, on average

In [4]:
shop_avg = df.groupby('shop')[['cpc_250g','cpc_1kg']].mean().round(2)
shop_avg = shop_avg.sort_values(by='cpc_1kg')
shop_avg = shop_avg.reset_index()
#shop_avg.dtypes

fig = px.bar(shop_avg, x='shop', y='cpc_1kg', title='Average cost per cup (when buying 1kg bags)', text_auto=True)
fig.show()

# Type: Single origin vs blend

Single origin tends to be more expensive than blends, but how much more?

In [5]:
types = df.groupby('type')[['cpc_250g','cpc_1kg']].mean()
types = types.sort_values(by='cpc_250g')
types = types.reset_index()
types

type  cpc_250g   cpc_1kg
0  blend  0.773500  0.676000
1     so  1.049545  0.924545

In [6]:
df_type = df
fig = px.box(df_type, x='type', y='cpc_1kg', title='Single origin vs blend')
fig.update_layout(xaxis_title='type', yaxis_title='cpc_1kg')
fig.show()

In [7]:
mean_price_per_type = types.groupby('type')['cpc_250g'].mean()
blend_price = mean_price_per_type['blend']
so_price = mean_price_per_type['so']
percentage_difference = ((so_price - blend_price) / blend_price) * 100
print("Single origin is {:.2f}% more expensive than Blend, on average.".format(percentage_difference))

Single origin is 35.69% more expensive than Blend, on average.


# Process
- Natural Process: Coffee cherries are dried whole, allowing the fruit to ferment around the bean, imparting fruity flavors.
- Washed Process: Coffee cherries are pulped to remove the fruit, then fermented in water to remove mucilage before drying, resulting in a clean cup with bright acidity.
- Honey Process: Coffee cherries are pulped but some or all of the mucilage is left on the beans during drying, leading to varying degrees of sweetness and body.
- Anaerobic Process: Coffee cherries are placed in a sealed container to ferment in the absence of oxygen, resulting in unique and complex flavor profiles due to controlled fermentation conditions.

Natural and washed are by far the most common. Unless explicitely mentioned, all blends are usually a combination of natural and washed, and marked as (mixed).

In [8]:
process = df.groupby('process').agg({'process': 'count', 'cpc_250g': 'mean', 'cpc_1kg': 'mean'})
process.rename(columns={'process': 'count'}, inplace=True)
process = process.sort_values(by='count', ascending=False)
process = process.reset_index()
process

process  count  cpc_250g   cpc_1kg
0     washed     33  1.053030  0.931212
1    natural     25  1.046800  0.925600
2    (mixed)      9  0.781111  0.692222
3      honey      5  1.116000  0.932000
4  anaerobic      2  1.200000  1.110000
5  sugarcane      1  0.860000  0.770000

In [9]:
df_process = df[df['type'] == 'so']
fig = px.box(df_process, x='process', y='cpc_1kg', title='Distribution of Coffee Prices by process (single origin only)')
fig.update_layout(xaxis_title='process', yaxis_title='cpc_1kg', xaxis_tickangle=-45)
fig.show()